In [1]:
%cd ..

/Users/ishamrashik/Desktop/machine-learning-and-ai-projects/community-mcp-session/aws_community_day/youtube-sentiment-insights


In [2]:
import mlflow
import os 

# Set AWS credentials (replace with your actual credentials)
os.environ['AWS_ACCESS_KEY_ID'] = os.getenv('AWS_ACCESS_KEY_ID')
os.environ['AWS_SECRET_ACCESS_KEY'] = os.getenv('AWS_SECRET_ACCESS_KEY')
os.environ['AWS_DEFAULT_REGION'] = os.getenv('AWS_DEFAULT_REGION')

# Then set MLflow tracking URI
mlflow.set_tracking_uri("http://3.29.137.20:5000")

In [3]:
# Set or create an experiment
mlflow.set_experiment("LightGBM HP Tuning")

2025/10/12 19:18:07 INFO mlflow.tracking.fluent: Experiment with name 'LightGBM HP Tuning' does not exist. Creating a new experiment.


<Experiment: artifact_location='s3://mlflow-artifacts-5fb77f1c/688158500548363559', creation_time=1760282287992, experiment_id='688158500548363559', last_update_time=1760282287992, lifecycle_stage='active', name='LightGBM HP Tuning', tags={}>

In [5]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report
from imblearn.over_sampling import SMOTE
import mlflow
import mlflow.sklearn
import optuna
from lightgbm import LGBMClassifier
import matplotlib.pyplot as plt

In [6]:
from utilities import load_data, INTERIM_DATA_PATH

In [9]:
train_df_path = os.path.join(INTERIM_DATA_PATH, "train_processed.csv")
val_df_path = os.path.join(INTERIM_DATA_PATH, "val_processed.csv")
test_df_path = os.path.join(INTERIM_DATA_PATH, "test_processed.csv")

train_df = load_data(train_df_path)
val_df = load_data(val_df_path)
test_df = load_data(test_df_path)

2025-10-12 19:20:20,889 - model_building - DEBUG - Data loaded from data/interim/train_processed.csv


2025-10-12 19:20:20,894 - model_building - DEBUG - Data loaded from data/interim/val_processed.csv
2025-10-12 19:20:20,900 - model_building - DEBUG - Data loaded from data/interim/test_processed.csv


In [10]:
ngram_range = (1, 3)  # Trigram setting
max_features = 10000  # Set max_features to 1000 for TF-IDF

# Step 2: Vectorization using TF-IDF, fit on training data only
vectorizer = TfidfVectorizer(ngram_range=ngram_range, max_features=max_features)

# Step 1: Vectorize the text comments (Bag of Words)
X_train_text = vectorizer.fit_transform(train_df['clean_comment']).toarray()
X_val_text = vectorizer.transform(val_df['clean_comment']).toarray()

# Step 2: Extract numerical features
# Define the numerical feature columns to include
numerical_features = ['word_count', 'num_stop_words', 'num_chars', 'num_chars_cleaned']

X_train_numerical = train_df[numerical_features].values
X_val_numerical = val_df[numerical_features].values

# Step 3: Combine text features with numerical features
import numpy as np

X_train = np.hstack([X_train_text, X_train_numerical])
X_val = np.hstack([X_val_text, X_val_numerical])

# Target variable
y_train = train_df['category']
y_val = val_df['category']

smote = SMOTE(random_state=42)
X_train, y_train = smote.fit_resample(X_train, y_train)

In [ ]:
# Function to log results in MLflow
def log_mlflow(model_name, model, X_train, X_val, y_train, y_val, params, trial_number):
    with mlflow.start_run():
        # Log model type and trial number
        mlflow.set_tag("mlflow.runName", f"Trial_{trial_number}_{model_name}_SMOTE_TFIDF_Trigrams")
        mlflow.set_tag("experiment_type", "algorithm_comparison")

        # Log algorithm name as a parameter
        mlflow.log_param("algo_name", model_name)

        # Log hyperparameters
        for key, value in params.items():
            mlflow.log_param(key, value)

        # Train model
        model.fit(X_train, y_train)
        y_pred = model.predict(X_val)

        # Log accuracy
        accuracy = accuracy_score(y_val, y_pred)
        mlflow.log_metric("accuracy", accuracy)

        # Log classification report
        classification_rep = classification_report(y_val, y_pred, output_dict=True)
        for label, metrics in classification_rep.items():
            if isinstance(metrics, dict):
                for metric, value in metrics.items():
                    mlflow.log_metric(f"{label}_{metric}", value)

        # Log the model
        mlflow.sklearn.log_model(model, f"{model_name}_model")

        return accuracy

In [13]:
# Step 6: Optuna objective function for LightGBM
def objective_lightgbm(trial):
    # Hyperparameter space to explore
    n_estimators = trial.suggest_int('n_estimators', 100, 1000)
    learning_rate = trial.suggest_float('learning_rate', 1e-4, 1e-1, log=True)
    max_depth = trial.suggest_int('max_depth', 3, 15)
    num_leaves = trial.suggest_int('num_leaves', 20, 150)
    min_child_samples = trial.suggest_int('min_child_samples', 10, 100)
    colsample_bytree = trial.suggest_float('colsample_bytree', 0.5, 1.0)
    subsample = trial.suggest_float('subsample', 0.5, 1.0)
    reg_alpha = trial.suggest_float('reg_alpha', 1e-4, 10.0, log=True)  # L1 regularization
    reg_lambda = trial.suggest_float('reg_lambda', 1e-4, 10.0, log=True)  # L2 regularization

    # Log trial parameters
    params = {
        'n_estimators': n_estimators,
        'learning_rate': learning_rate,
        'max_depth': max_depth,
        'num_leaves': num_leaves,
        'min_child_samples': min_child_samples,
        'colsample_bytree': colsample_bytree,
        'subsample': subsample,
        'reg_alpha': reg_alpha,
        'reg_lambda': reg_lambda
    }

    # Create LightGBM model
    model = LGBMClassifier(n_estimators=n_estimators,
                           learning_rate=learning_rate,
                           max_depth=max_depth,
                           num_leaves=num_leaves,
                           min_child_samples=min_child_samples,
                           colsample_bytree=colsample_bytree,
                           subsample=subsample,
                           reg_alpha=reg_alpha,
                           reg_lambda=reg_lambda,
                           random_state=42)

    # Log each trial as a separate run in MLflow
    accuracy = log_mlflow("LightGBM", model, X_train, X_val, y_train, y_val, params, trial.number)

    return accuracy



In [14]:
# Step 7: Run Optuna for LightGBM, log the best model, and plot the importance of each parameter
def run_optuna_experiment():
    study = optuna.create_study(direction="maximize")
    study.optimize(objective_lightgbm, n_trials=100)  # Increased to 100 trials

    # Get the best parameters
    best_params = study.best_params
    best_model = LGBMClassifier(n_estimators=best_params['n_estimators'],
                                learning_rate=best_params['learning_rate'],
                                max_depth=best_params['max_depth'],
                                num_leaves=best_params['num_leaves'],
                                min_child_samples=best_params['min_child_samples'],
                                colsample_bytree=best_params['colsample_bytree'],
                                subsample=best_params['subsample'],
                                reg_alpha=best_params['reg_alpha'],
                                reg_lambda=best_params['reg_lambda'],
                                random_state=42)

    # Log the best model with MLflow and print the classification report
    log_mlflow("LightGBM", best_model, X_train, X_val, y_train, y_val, best_params, "Best")

    # Plot parameter importance
    optuna.visualization.plot_param_importances(study).show()

    # Plot optimization history
    optuna.visualization.plot_optimization_history(study).show()

In [ ]:
# Run the experiment for LightGBM
run_optuna_experiment()

[I 2025-10-12 19:22:02,485] A new study created in memory with name: no-name-b5113580-f9fd-45e1-9366-ecb2fdb6a035


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.099641 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 119160
[LightGBM] [Info] Number of data points in the train set: 23397, number of used features: 1813
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further

/opt/homebrew/Caskroom/miniforge/base/envs/mlops_aws_community/lib/python3.12/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
2025/10/12 19:22:16 WARNING mlflow.models.model: `artifact_path` is deprecated. Please use `name` instead.
2025/10/12 19:22:18 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
[I 2025-10-12 19:22:19,410] Trial 0 finished with value: 0.5875769445998881 and parameters: {'n_estimators': 246, 'learning_rate': 0.0005639336751050803, 'max_depth': 14, 'num_leaves': 62, 'min_child_samples': 64, 'colsample_bytree': 0.9949638648840109, 'subsample': 0.7148386862154588, 'reg_alpha': 0.0002134627272484808, 'reg_lambda': 2.579866935078037}. Best is trial 0 with value: 0.5875769445998881.


🏃 View run Trial_0_LightGBM_SMOTE_TFIDF_Trigrams at: http://3.29.137.20:5000/#/experiments/688158500548363559/runs/5496f7975a43433f992042f100ea949e
🧪 View experiment at: http://3.29.137.20:5000/#/experiments/688158500548363559
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.119432 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 125378
[LightGBM] [Info] Number of data points in the train set: 23397, number of used features: 2122
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No furth

/opt/homebrew/Caskroom/miniforge/base/envs/mlops_aws_community/lib/python3.12/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
2025/10/12 19:22:26 WARNING mlflow.models.model: `artifact_path` is deprecated. Please use `name` instead.
2025/10/12 19:22:27 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
[I 2025-10-12 19:22:28,084] Trial 1 finished with value: 0.6944599888080581 and parameters: {'n_estimators': 586, 'learning_rate': 0.023208376081236694, 'max_depth': 4, 'num_leaves': 34, 'min_child_samples': 57, 'colsample_bytree': 0.7890174948017576, 'subsample': 0.6034459594604498, 'reg_alpha': 0.17753851215132846, 'reg_lambda': 0.2586018313798269}. Best is trial 1 with value: 0.6944599888080581.


...

🏃 View run Trial_45_LightGBM_SMOTE_TFIDF_Trigrams at: http://3.29.137.20:5000/#/experiments/688158500548363559/runs/868beefba6944721a9fc6643467ea51d
🧪 View experiment at: http://3.29.137.20:5000/#/experiments/688158500548363559
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.188269 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 145409
[LightGBM] [Info] Number of data points in the train set: 23397, number of used features: 3409
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warni

Exception ignored on calling ctypes callback function: <function _log_callback at 0x14d7eafc0>
Traceback (most recent call last):
  File "/opt/homebrew/Caskroom/miniforge/base/envs/mlops_aws_community/lib/python3.12/site-packages/lightgbm/basic.py", line 287, in _log_callback
    def _log_callback(msg: bytes) -> None:
    
KeyboardInterrupt: 


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with po

/opt/homebrew/Caskroom/miniforge/base/envs/mlops_aws_community/lib/python3.12/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
2025/10/12 19:43:17 WARNING mlflow.models.model: `artifact_path` is deprecated. Please use `name` instead.
2025/10/12 19:43:19 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
[I 2025-10-12 19:43:21,028] Trial 46 finished with value: 0.7129266927811976 and parameters: {'n_estimators': 946, 'learning_rate': 0.013961400386068315, 'max_depth': 9, 'num_leaves': 111, 'min_child_samples': 34, 'colsample_bytree': 0.8217441927378564, 'subsample': 0.8200522051436397, 'reg_alpha': 4.536858643747722, 'reg_lambda': 0.06642272775289775}. Best is trial 42 with value: 0.7470621152770005.


🏃 View run Trial_46_LightGBM_SMOTE_TFIDF_Trigrams at: http://3.29.137.20:5000/#/experiments/688158500548363559/runs/bf47680c6ee44235b827975cd411d0d5
🧪 View experiment at: http://3.29.137.20:5000/#/experiments/688158500548363559
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.137187 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 131200
[LightGBM] [Info] Number of data points in the train set: 23397, number of used features: 2434
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warni